In [0]:
%run ../_utils

Note: you may need to restart the kernel using dbutils.library.restartPython() to use updated packages.
Note: you may need to restart the kernel using dbutils.library.restartPython() to use updated packages.


In [0]:
from pyspark.sql.functions import when, to_date, col, dayofweek
from pyspark.sql.types import StringType, BooleanType


# Camada Silver

Na camada silver, limpezas e ajustes em dados devem ser aplicados

Caso seja possível, enriquecer os dados e extrair dados também deve acontecer nessa camada (minha definição)

In [0]:
tb_name = "olist_silver.customers"
dataset_location = "olist_customers_dataset"
target_location = f"dbfs:/FileStore/delta/brazilian_ecommerce/{dataset_location}/silver"

## 1 - Data ingestion

In [0]:
df = spark.read.table("olist_bronze.customers") # leituira da delta table

In [0]:
df.printSchema()

root
 |-- customer_id: string (nullable = true)
 |-- customer_unique_id: string (nullable = true)
 |-- customer_zip_code_prefix: integer (nullable = true)
 |-- customer_city: string (nullable = true)
 |-- customer_state: string (nullable = true)



In [0]:
display(df)

customer_id customer_unique_id customer_zip_code_prefix customer_city customer_state 06b8999e2fba1a1fbc88172c00ba8bc7 861eff4711a542e4b93843c6dd7febb0 14409 franca SP 18955e83d337fd6b2def6b18a428ac77 290c77bc529b7ac935b93aa66c333dc3 9790 sao bernardo do campo SP 4e7b3e00288586ebd08712fdd0374a03 060e732b5b29e8181a18229c7b0b2b5e 1151 sao paulo SP b2b6027bc5c5109e529d4dc6358b12c3 259dac757896d24d7702b9acbbff3f3c 8775 mogi das cruzes SP 4f2d8ab171c80ec8364f7c12e35b23ad 345ecd01c38d18a9036ed96c73b8d066 13056 campinas SP 879864dab9bc3047522c92c82e1212b8 4c93744516667ad3b8f1fb645a3116a4 89254 jaragua do sul SC fd826e7cf63160e536e0908c76c3f441 addec96d2e059c80c30fe6871d30d177 4534 sao paulo SP 5e274e7a0c3809e14aba7ad5aae0d407 57b2a98a409812fe9618067b6b8ebe4f 35182 timoteo MG 5adf08e34b2e993982a47070956c5c65 1175e95fb47ddff9de6b2b06188f7e0d 81560 curitiba PR 4b7139f34592b3a31687243a302fa75b 9afe194fb833f79e300e37e580171f22 30575 belo horizonte MG 9fb35e4ed6f0a14a4977cd9aea4042bb 2a7745e1ed516b289ed9b29c7d0539a5 39400 montes claros MG 5aa9e4fdd4dfd20959cad2d772509598 2a46fb94aef5cbeeb850418118cee090 20231 rio de janeiro RJ b2d1536598b73a9abd18e0d75d92f0a3 918dc87cd72cd9f6ed4bd442ed785235 18682 lencois paulista SP eabebad39a88bb6f5b52376faec28612 295c05e81917928d76245e842748184d 5704 sao paulo SP 1f1c7bf1c9b041b292af6c1c4470b753 3151a81801c8386361b62277d7fa5ecf 95110 caxias do sul RS 206f3129c0e4d7d0b9550426023f0a08 21f748a16f4e1688a9014eb3ee6fa325 13412 piracicaba SP a7c125a0a07b75146167b7f04a7f8e98 5c2991dbd08bbf3cf410713c4de5a0b5 22750 rio de janeiro RJ c5c61596a3b6bd0cee5766992c48a9a1 b6e99561fe6f34a55b0b7da92f8ed775 7124 guarulhos SP 9b8ce803689b3562defaad4613ef426f 7f3a72e8f988c6e735ba118d54f47458 5416 sao paulo SP 49d0ea0986edde72da777f15456a0ee0 3e6fd6b2f0d499456a6a6820a40f2d79 68485 pacaja PA 154c4ded6991bdfa3cd249d11abf4130 e607ede0e63436308660236f5a52da5e 88034 florianopolis SC 690172ab319622688d3b4df42f676898 a96d5cfa0d3181817e2b946f921ea021 74914 aparecida de goiania GO 2938121a40a20953c43caa8c98787fcb 482441ea6a06b1f72fe9784756c0ea75 5713 sao paulo SP 237098a64674ae89babdc426746260fc 4390ddbb6276a66ff1736a6710205dca 82820 curitiba PR cb721d7b4f271fd87011c4c83462c076 a5844ba4bfc8d0cc61d13027c7e63bcc 8225 sao paulo SP f681356046d9fde60e70c73a18d65ea2 5f102dd37243f152aec3607970aad100 9121 santo andre SP 167bd30a409e3e4127df5a9408ebd394 9c0096673baf55453a50073f12d1a37f 74310 goiania GO 6e359a57a91f84095cc64e1b351aef8c 2e6a42a9b5cbb0da62988694f18ee295 4571 sao paulo SP e0eea8f69a457b3f1fa246e44c9ebefd 4d221875624017bc47b4d1ce7314a5b7 29311 cachoeiro de itapemirim ES e3109970a3fe8021d5ff82c577ce5606 a8654e2af5da6bb72f52c22b164855e1 5528 sao paulo SP 261cb4f92498ca05d5bd1a327a261d9c 424aca6872c5bab80780a8dec03b7516 12235 sao jose dos campos SP 6f92779347724b67e44e3224f3b4cffd bf4862777db128507e9efcc789215e9b 18130 sao roque SP 2d5831cb2dff7cdefba62e950ae3dc7b e9dd12dca17352644a959d9dea133935 42800 camacari BA b2bed119388167a954382cca36c4777f e079b18794454de9d2be5c12b4392294 27525 resende RJ 469634941c27cd844170935a3cf60b95 ef07ba9aa5226f77264ffa5762b2280b 81750 curitiba PR df0aa5b8586495e0ddf6b601122e43a1 85d234692f7bee8d6fea586e237334b6 13175 sumare SP 41c8f4b570869791379a925899a6af8a fe3634ccefbcdb0537b45fd589e32e8e 7170 guarulhos SP 54f755c3fd2709231f9964a1430c5218 40febde16f4718a5def537786473b0be 93415 novo hamburgo RS 4c06b42fbf7b97ab10779cda5549cd1c 07d190f123147d9e89d4b922543d7948 65075 sao luis MA b6368ca0f56d4632f44d58ca431487b2 dd992305cba295d997f263dbdf4e8c2e 88104 sao jose SC 4a0e66fd30684aa1409cd1b66fec77cc 86085586aaa8c5f47ed0b400da64c59d 7176 guarulhos SP c168abb9077b7821adae01dc1f0886c5 5ad58a4e6a1a656b6bed070cadbaa003 35960 santa barbara MG a3b0fda37bae14cf754877bed475e80c c9158d089637ab443c78984d20da7fc0 5727 sao paulo SP 0ccd415657ae8a6cd1c71b00155a019e 66cc90195ca44cc7ac6a1cd0e1e1e7b2 7053 guarulhos SP c532a74a3ebf1bacce2e2bcce3783317 91ec50a00ae74d0a229d2efdf4344e1e 14026 ribeirao preto SP 19cecb194f54e614b70d


## 2 - Data Cleaning

Aqui nessa table os dados já estão limpos e tratados. Somente iremos armazenar e criar a delta table


## Saving data

In [0]:
save_dataframe(df, format_mode="delta", table_name=tb_name, target_location=target_location)

[LOG] Saving olist_silver.customers delta on dbfs:/FileStore/delta/brazilian_ecommerce/olist_customers_dataset/silver... OK!



## create delta table

TODO: implementar UPSERT

o upsert serve para não precisar reescrever todos os dados, mas aproveitar do Delta para fazer um MERGE, caso um registro antigo tenha uma nova versão e INSERT para os dados que são novos

In [0]:
create_table(table_name=tb_name, target_location=target_location)

[LOG] Creating delta table olist_silver.customers on dbfs:/FileStore/delta/brazilian_ecommerce/olist_customers_dataset/silver... OK!


In [0]:
# exit para fechar a execução
dbutils.notebook.exit("OK")

In [0]:
%sql

select * from olist_silver.customers

customer_id customer_unique_id customer_zip_code_prefix customer_city customer_state 06b8999e2fba1a1fbc88172c00ba8bc7 861eff4711a542e4b93843c6dd7febb0 14409 franca SP 18955e83d337fd6b2def6b18a428ac77 290c77bc529b7ac935b93aa66c333dc3 9790 sao bernardo do campo SP 4e7b3e00288586ebd08712fdd0374a03 060e732b5b29e8181a18229c7b0b2b5e 1151 sao paulo SP b2b6027bc5c5109e529d4dc6358b12c3 259dac757896d24d7702b9acbbff3f3c 8775 mogi das cruzes SP 4f2d8ab171c80ec8364f7c12e35b23ad 345ecd01c38d18a9036ed96c73b8d066 13056 campinas SP 879864dab9bc3047522c92c82e1212b8 4c93744516667ad3b8f1fb645a3116a4 89254 jaragua do sul SC fd826e7cf63160e536e0908c76c3f441 addec96d2e059c80c30fe6871d30d177 4534 sao paulo SP 5e274e7a0c3809e14aba7ad5aae0d407 57b2a98a409812fe9618067b6b8ebe4f 35182 timoteo MG 5adf08e34b2e993982a47070956c5c65 1175e95fb47ddff9de6b2b06188f7e0d 81560 curitiba PR 4b7139f34592b3a31687243a302fa75b 9afe194fb833f79e300e37e580171f22 30575 belo horizonte MG 9fb35e4ed6f0a14a4977cd9aea4042bb 2a7745e1ed516b289ed9b29c7d0539a5 39400 montes claros MG 5aa9e4fdd4dfd20959cad2d772509598 2a46fb94aef5cbeeb850418118cee090 20231 rio de janeiro RJ b2d1536598b73a9abd18e0d75d92f0a3 918dc87cd72cd9f6ed4bd442ed785235 18682 lencois paulista SP eabebad39a88bb6f5b52376faec28612 295c05e81917928d76245e842748184d 5704 sao paulo SP 1f1c7bf1c9b041b292af6c1c4470b753 3151a81801c8386361b62277d7fa5ecf 95110 caxias do sul RS 206f3129c0e4d7d0b9550426023f0a08 21f748a16f4e1688a9014eb3ee6fa325 13412 piracicaba SP a7c125a0a07b75146167b7f04a7f8e98 5c2991dbd08bbf3cf410713c4de5a0b5 22750 rio de janeiro RJ c5c61596a3b6bd0cee5766992c48a9a1 b6e99561fe6f34a55b0b7da92f8ed775 7124 guarulhos SP 9b8ce803689b3562defaad4613ef426f 7f3a72e8f988c6e735ba118d54f47458 5416 sao paulo SP 49d0ea0986edde72da777f15456a0ee0 3e6fd6b2f0d499456a6a6820a40f2d79 68485 pacaja PA 154c4ded6991bdfa3cd249d11abf4130 e607ede0e63436308660236f5a52da5e 88034 florianopolis SC 690172ab319622688d3b4df42f676898 a96d5cfa0d3181817e2b946f921ea021 74914 aparecida de goiania GO 2938121a40a20953c43caa8c98787fcb 482441ea6a06b1f72fe9784756c0ea75 5713 sao paulo SP 237098a64674ae89babdc426746260fc 4390ddbb6276a66ff1736a6710205dca 82820 curitiba PR cb721d7b4f271fd87011c4c83462c076 a5844ba4bfc8d0cc61d13027c7e63bcc 8225 sao paulo SP f681356046d9fde60e70c73a18d65ea2 5f102dd37243f152aec3607970aad100 9121 santo andre SP 167bd30a409e3e4127df5a9408ebd394 9c0096673baf55453a50073f12d1a37f 74310 goiania GO 6e359a57a91f84095cc64e1b351aef8c 2e6a42a9b5cbb0da62988694f18ee295 4571 sao paulo SP e0eea8f69a457b3f1fa246e44c9ebefd 4d221875624017bc47b4d1ce7314a5b7 29311 cachoeiro de itapemirim ES e3109970a3fe8021d5ff82c577ce5606 a8654e2af5da6bb72f52c22b164855e1 5528 sao paulo SP 261cb4f92498ca05d5bd1a327a261d9c 424aca6872c5bab80780a8dec03b7516 12235 sao jose dos campos SP 6f92779347724b67e44e3224f3b4cffd bf4862777db128507e9efcc789215e9b 18130 sao roque SP 2d5831cb2dff7cdefba62e950ae3dc7b e9dd12dca17352644a959d9dea133935 42800 camacari BA b2bed119388167a954382cca36c4777f e079b18794454de9d2be5c12b4392294 27525 resende RJ 469634941c27cd844170935a3cf60b95 ef07ba9aa5226f77264ffa5762b2280b 81750 curitiba PR df0aa5b8586495e0ddf6b601122e43a1 85d234692f7bee8d6fea586e237334b6 13175 sumare SP 41c8f4b570869791379a925899a6af8a fe3634ccefbcdb0537b45fd589e32e8e 7170 guarulhos SP 54f755c3fd2709231f9964a1430c5218 40febde16f4718a5def537786473b0be 93415 novo hamburgo RS 4c06b42fbf7b97ab10779cda5549cd1c 07d190f123147d9e89d4b922543d7948 65075 sao luis MA b6368ca0f56d4632f44d58ca431487b2 dd992305cba295d997f263dbdf4e8c2e 88104 sao jose SC 4a0e66fd30684aa1409cd1b66fec77cc 86085586aaa8c5f47ed0b400da64c59d 7176 guarulhos SP c168abb9077b7821adae01dc1f0886c5 5ad58a4e6a1a656b6bed070cadbaa003 35960 santa barbara MG a3b0fda37bae14cf754877bed475e80c c9158d089637ab443c78984d20da7fc0 5727 sao paulo SP 0ccd415657ae8a6cd1c71b00155a019e 66cc90195ca44cc7ac6a1cd0e1e1e7b2 7053 guarulhos SP c532a74a3ebf1bacce2e2bcce3783317 91ec50a00ae74d0a229d2efdf4344e1e 14026 ribeirao preto SP 19cecb194f54e614b70d